<img src="./images/DLI_Header.png" width=400/>

# Fundamentals of Accelerated Data Science # 

## 03 - DBSCAN ##

**Table of Contents**
<br>
This notebook uses GPU-accelerated DBSCAN to identify clusters of infected people. This notebook covers the below sections: 
1. [Environment](#Environment)
2. [Load Data](#Load-Data)
3. [DBSCAN Clustering](#DBSCAN-Clustering)
    * [Exercise #1 - Make Another DBSCAN Instance](#Exercise-#1---Make-Another-DBSCAN-Instance)
4. [Visualize the Clusters](#Visualize-the-Clusters)

## Environment ##

In [2]:
import cudf
import cuml

import cuxfilter as cxf

## Load Data ##
For this notebook, we again load a subset of our population data with only the columns we need. An `infected` column has been added to the data to indicate whether or not a person is known to be infected with our simulated virus.

In [3]:
gdf = cudf.read_csv('./data/pop_sample.csv', dtype=['float32', 'float32', 'float32'])
print(gdf.dtypes)
gdf.shape

northing    float32
easting     float32
infected    float32
dtype: object


(1000000, 3)

In [4]:
gdf.head()

northing      easting  infected
0  178547.296875  368012.1250       0.0
1  174068.281250  543802.1250       0.0
2  358293.687500  435639.8750       0.0
3   87240.304688  389607.3750       0.0
4  158261.015625  340764.9375       0.0

In [5]:
gdf['infected'].value_counts()

infected
0.0    984331
1.0     15669
Name: count, dtype: int64

## DBSCAN Clustering ##
DBSCAN is another unsupervised clustering algorithm that is particularly effective when the number of clusters is not known up front and the clusters may have concave or other unusual shapes--a situation that often applies in geospatial analytics.

In this series of exercises you will use DBSCAN to identify clusters of infected people by location, which may help us identify groups becoming infected from common patient zeroes and assist in response planning.

Create a DBSCAN instance by using `cuml.DBSCAN`. Pass in the named argument `eps` (the maximum distance a point can be from the nearest point in a cluster to be considered possibly in that cluster) to be `5000`. Since the `northing` and `easting` values we created are measured in meters, this will allow us to identify clusters of infected people where individuals may be separated from the rest of the cluster by up to 5 kilometers.

Below we train a DBSCAN algorithm. We start by creating a new dataframe from rows of the original dataframe where `infected` is `1` (true), and call it `infected_df`--be sure to reset the dataframe's index afterward. Use `dbscan.fit_predict` to perform clustering on the `northing` and `easting` columns of `infected_df`, and turn the resulting series into a new column in `infected_gdf` called "cluster". Finally, compute the number of clusters identified by DBSCAN.

In [6]:
dbscan = cuml.DBSCAN(eps=5000)
# dbscan = cuml.DBSCAN(eps=10000)

infected_df = gdf[gdf['infected'] == 1].reset_index()
infected_df['cluster'] = dbscan.fit_predict(infected_df[['northing', 'easting']])
infected_df['cluster'].nunique()

96

### Exercise #1 - Make Another DBSCAN Instance ###

**Instructions**: <br>
* Modify the `<FIXME>` only and execute the below cell to instantiate a DBSCAN instance with `10000` for `eps`.
* Modify the `<FIXME>` only and execute the cell below to fit the data and identify infected clusters. 

In [ ]:
dbscan = cuml.DBSCAN(<<<<FIXME>>>>)

In [ ]:
infected_df = gdf[gdf['infected'] == 1].reset_index()
infected_df['cluster'] = dbscan.<<<<FIXME>>>>(infected_df[['northing', 'easting']])
infected_df['cluster'].nunique()

Click ... for solution. 

## Visualize the Clusters

In [ ]:
import cudf
import cuml
from pyproj import Transformer
from colorcet import glasbey # палитра цветов
import cuxfilter
from cuxfilter import charts

dbscan = cuml.DBSCAN(eps = 8150, min_samples = 13)

# только строки infected = 1 и заново индексируем
infected_df = gdf[gdf['infected'] == 1].reset_index(drop=True)
infected_df['cluster'] = dbscan.fit_predict(
    infected_df[['northing', 'easting']]
)

# убираем шумы на графике
# infected_df = infected_df[infected_df['cluster'] != -1].reset_index(drop=True)

print(infected_df['cluster'].value_counts().sort_index())

transformer = Transformer.from_crs("epsg:27700", "epsg:3857", always_xy=True)

pdf = infected_df.to_pandas()
pdf["wm_easting"], pdf["wm_northing"] = transformer.transform(
    pdf["easting"].values,
    pdf["northing"].values,
)

# у каждого больного вес = 1
pdf["weight"] = 1

infected_df = cudf.from_pandas(pdf)

# оборачиваем датафрейм в объект cuxfilter, чтобы библиотека могла с ним работать
cux_df = cuxfilter.DataFrame.from_dataframe(infected_df)

# cuxfilter требует gpu
# подсчет уникальных кластеров
cluster_vals = infected_df["cluster"].to_pandas().sort_values().unique()
n_clusters = len(cluster_vals)
# автоматическая генерация цветов для n кластеров
palette_clusters = list(glasbey[:n_clusters])

clusters_chart = charts.scatter(
    x="wm_easting",
    y="wm_northing",
    aggregate_col="cluster",
    aggregate_fn="mean",
    tile_provider="CartoLight",
    pixel_shade_type="linear",
    color_palette=palette_clusters,
    point_size=10,
    point_shape="circle",
    title="Infected people clusters",
)

density_chart = charts.heatmap(
    x="wm_easting",
    y="wm_northing",
    aggregate_col="weight", # используем колонку с единицами
    aggregate_fn="sum", # суммируем единицы
    title="Infected People Density",
)

cluster_multi_select = charts.multi_select("cluster")

dashboard = cux_df.dashboard(
    charts=[clusters_chart, density_chart],
    sidebar=[cluster_multi_select],
    layout=cuxfilter.layouts.double_feature, # 2 графика (добавилась тепловая карта плоскости)
    theme=cuxfilter.themes.dark,
    title="Dashboard",
    data_size_widget=True,
)

dashboard.app()

cluster
-1      1392
 0     12906
 1       628
 2        54
 3       159
 4        37
 5       138
 6        90
 7        33
 8        42
 9        74
 10        3
 11       25
 12       14
 13       13
 14       13
 15        7
 16       21
 17       10
 18       10
Name: count, dtype: int64


GridSpec(ncols=12, nrows=5)
    [0] GridSpec(height=800, ncols=12, nrows=5, sizing_mode='fixed', width=1200)
        [0] HoloViews(DynamicMap, height=800, sizing_mode='stretch_both', width=600)
        [1] HoloViews(DynamicMap, height=800, sizing_mode='stretch_both', width=600)
    [1] WidgetBox(styles={'border-color': '...})
        [0] Number(css_classes=['indicator'], default_color='#2B2B2B', font_size='18pt', format='{value:,}', name='Datapoints Selected', sizing_mode='stretch_width', title_size='14pt', value=15669)
        [1] Progress(sizing_mode='stretch_width', styles={'--success-bg-color': '...}, value=100)
    [2] Column(min_height=500, sizing_mode='stretch_width')
        [0] MultiChoice(name='cluster', options=[-1, 0, 5, 1, ...], sizing_mode='scale_width', styles={'color': '#2B2B2B'}, stylesheets=['\n                .choic...])

Because we have the same column names as in the K-means example--`easting`, `northing`, and `cluster`--we can use the same code to visualize the clusters.

In [ ]:
infected_df.to_pandas().plot(kind='scatter', x='easting', y='northing', c='cluster')

In [ ]:
import IPython
app = IPython.Application.instance()
app.kernel.do_shutdown(True)

**Well Done!** Let's move to the [next notebook](3-04_logistic_regression.ipynb). 

<img src="./images/DLI_Header.png" width=400/>